In [2]:
from typing import Dict

from agent.models.agent import MultiAgentSearchLocalNode


def create_local_nodes_map(lexical_graph) -> Dict[str, MultiAgentSearchLocalNode]:
    local_nodes_map: Dict[str, MultiAgentSearchLocalNode] = {}
    for node, data in lexical_graph.nodes(data=True):
        print(f"Processing node: {node}")
        content = (
            data["content"]
            if "content" in data and data["content"] != ""
            else "(empty content)"
        )
        if len(content) > 10000:
            content = content[:10000] + "..."
        local_nodes_map[node] = MultiAgentSearchLocalNode(
            unique_id=node,
            content=content,
        )
    return local_nodes_map

In [3]:
from graph.lexical import LexicalGraphBuilder
from llama_index.embeddings.openai import OpenAIEmbedding
from llama_index.core.retrievers import VectorIndexRetriever

lexical_graph = LexicalGraphBuilder(
    file_name="./kifrs_result.json", upload_new_csvs_on_build=True
).build_graph()
local_nodes_map = create_local_nodes_map(lexical_graph)


Processing node: 1000
Creating node with id 1000 재무보고를 위한 개념체계
Processing node: 1000-XHKc8v
Creating node with id 1000-XHKc8v 본문
Processing node: 1000-IIXJKP
Creating node with id 1000-IIXJKP 재무보고를 위한 개념체계
Processing node: 1000-cBGbRE
Creating node with id 1000-cBGbRE 개념체계의 위상과 목적
Processing node: 1000-UNhjmD
Creating node with id 1000-UNhjmD 제1장 일반목적재무보고의 목적
Processing node: 1000-ZxcP1a
Creating node with id 1000-ZxcP1a 서론
Processing node: 1000-pWsM4G
Creating node with id 1000-pWsM4G 일반목적재무보고의 목적, 유용성 및 한계
Processing node: 1000-LA7fSy
Creating node with id 1000-LA7fSy 보고기업의 경제적자원, 청구권 그리고 자원 및 청구권의 변동에 관한 정보
Processing node: 1000-GrCAwu
Creating node with id 1000-GrCAwu 경제적자원 및 청구권
Processing node: 1000-WpwQ7V
Creating node with id 1000-WpwQ7V 경제적자원 및 청구권의 변동
Processing node: 1000-iWICjo
Creating node with id 1000-iWICjo 발생기준 회계가 반영된 재무성과
Processing node: 1000-VUt8r2
Creating node with id 1000-VUt8r2 과거 현금흐름이 반영된 재무성과
Processing node: 1000-PboWkY
Creating node with id 1000-PboWkY 재무성

In [5]:
from llama_index.core import VectorStoreIndex, StorageContext

storage_context = StorageContext.from_defaults()

openai_embeddings = OpenAIEmbedding(model="text-embedding-3-large")
vector_index = VectorStoreIndex(
    nodes=list(local_nodes_map.values()),
    storage_context=storage_context,
    embed_model=openai_embeddings,
)
vector_retriever = VectorIndexRetriever(index=vector_index, similarity_top_k=5)

In [14]:
from retriever.bm25 import BM25Retriever
from retriever.hybrid import VectorBM25

bm25_retriever = BM25Retriever(
    nodes=list(local_nodes_map.values()), similarity_top_k=20
)

retriever = VectorBM25( # type: ignore
    vector_retriever=vector_retriever, bm25_retriever=bm25_retriever
)

start indexing...
finished indexing within 321.302729845047 seconds


In [39]:


import importlib
import agent.main

# Reload the module
importlib.reload(agent.main)
from agent.main import Workflow
from agent.models.agent import AgentState



debug_markdown = "# Multi-Agent Log\n"
debug_markdown += "## Pass 1\n"





def multi_agent_query(query="How can the Board and the CCO manage control functions?"):
    initial_state = AgentState(
        query=query,
        definitions={},
        previous_nodes=[],
        last_fetched_context_nodes=[],
        node_links_to_fetch=[],
        node_footers_to_fetch={},
        allow_continue=True,
        search_failures=[],
        markdown_debug=debug_markdown,
        pass_count=1,
    )
    
    workflow = Workflow(lexical_graph=lexical_graph, retriever=retriever, local_nodes_map=local_nodes_map)
    graph = workflow.run()
    events = graph.stream(initial_state, {"recursion_limit": 150})
    for s in events:
        first_value = next(iter(s.values()))
    # return all of agent's references after answer
    return list(map(lambda node: node.id_, first_value["previous_nodes"])) + list(
        map(lambda node: node.id_, first_value["last_fetched_context_nodes"])
    )


multi_agent_query(
     "기업회계기준서 제1117호 ‘보험계약’ 문단 B96(4)[1]에 따르면, 미래 서비스 관련 비금융위험에 대한 위험조정의 변동을 ① 비금융위험과 관련된 변동과 ② 화폐의 시간가치 효과 및 그 변동의 효과로 구분하지 않고 해당 위험조정의 변동 전체를 보험계약마진으로 조정하는 방식을 선택할 수 있다. 위 문단을 근거로 하여 다수 보험사는 비금융위험에 대한 위험조정의 변동을 모두 보험계약마진에서 조정하는 회계처리하고 있다. (질의) 기업회계기준서 제1117호 문단 B96(4)에 따라 미래 서비스와 관련된 위험조정의 변동 전체를 보험계약마진으로 조정하기로 선택한 경우, 위험조정과 관련된 할인율의 변동 효과*를 회계처리하는 방법은? * 기업회계기준서 제1117호 B97(1)(다)[2]에서 기술하는 할인율의 변동효과(기초의 현행할인율과 기말의 현행할인율의 차이로 인한 효과)"
)


20
explore_response: {'node_ids_for_link_retrieval': ['`1117-101`', '`1117-B97`', '`1117-B96`', '`1117-BC276C`', '`1117-B113`', '`1117-BC19`']}
explore_response: {'node_ids_for_link_retrieval': ['`1117-56`', '`1117-59`', '`1117-B72`']}
explore_response: {'node_ids_for_link_retrieval': ['`1117-B89`', '`1117-B90`', '`1117-B86`']}
explore_response: {'node_ids_for_link_retrieval': ['`node_id_1`', '`node_id_2`', '`node_id_3`']}
response: 기업회계기준서 제1117호 문단 B96(4)에 따르면, 비금융위험에 대한 위험조정의 변동을 보험계약마진으로 조정하는 경우, 할인율의 변동 효과를 어떻게 회계처리하는지에 대한 방법은 문단 B97(1)(다)에서 다루어집니다. 이 문단에서 말하길, 미래 서비스와 관련된 이행현금흐름의 변동은 보험계약마진에서 조정하지 않고, 화폐의 시간가치 및 금융위험의 효과는 보험금융비용으로 인식되어야 하며, 이러한 변동과 관련된 효과들은 보험계약마진에서 제외된다고 명시합니다.

구체적으로, 문단 B97에서는 화폐의 시간가치와 금융위험, 그리고 할인율 변동의 효과를 개별적으로 보험계약마진에서 조정하지 않고, 이들 효과가 미치는 변동은 보험금융비용으로 처리한다고 설명합니다. 따라서 기업이 비금융위험에 대한 위험조정의 전체 변동을 보험계약마진에서 조정하기로 선택한 경우, 할인율의 변동 효과는 보험금융비용으로 인식되는 방법을 따르게 됩니다. 

즉, 위험조정과 관련된 할인율의 변동 효과는 보험계약마진이 아닌 보험금융비용으로 인식되어야 하며, 비금융위험에 대한 위험조정의 조정 자체는 보험계약마진에 포함되지만, 그에 따른 할

['1117-IE20',
 '1117-IE71',
 '1117-66',
 '1117-IE91',
 '1117-BC275',
 '1117-104',
 '1117-B97',
 '1117-BC276D',
 '1117-IE111',
 '1117-BC19',
 '1117-IE26',
 '1117-IE17',
 '1117-B113',
 '1117-B96',
 '1117-BC276C',
 '1117-BC279',
 '1117-53',
 '1117-54',
 '1117-55',
 '1117-56',
 '1117-57',
 '1117-58',
 '1117-59',
 '1117-69',
 '1117-70',
 '1117-70A',
 '1117-44',
 '1117-B72',
 '1117-B104',
 '1117-45',
 '1117-B115',
 '1117-BC147',
 '1117-BC159',
 '1117-BC160',
 '1117-BC161',
 '1117-BC162',
 '1117-BC163',
 '1117-BC164',
 '1117-BC165',
 '1117-BC166',
 '1117-BC167',
 '1117-BC168',
 '1117-BC169',
 '1117-BC170',
 '1117-BC170A',
 '1117-BC171',
 '1117-BC172',
 '1117-BC173',
 '1117-BC174',
 '1117-BC176',
 '1117-BC177',
 '1117-BC178',
 '1117-BC179',
 '1117-BC180',
 '1117-BC181',
 '1117-BC182',
 '1117-BC183',
 '1117-BC184',
 '1117-BC184A',
 '1117-BC184B',
 '1117-BC184C',
 '1117-BC184D',
 '1117-BC184E',
 '1117-BC184F',
 '1117-BC184G',
 '1117-BC184H',
 '1117-BC184I',
 '1117-BC184J',
 '1117-BC184K',
 '1117

In [35]:
import json


with open("./kifrs_queries.json", "r") as f:
    queries = json.load(f)

with open("./kifrs_result.json", "r") as f:
    documents = json.load(f)

def merge_ranks(paragraph_ids: list[str], data: dict) -> list[dict]:
    ranks = []
    for paragraph_id in paragraph_ids:
        try:
            content = data[paragraph_id]["fullContent"]
        except KeyError as e:
            continue
        ranks.append({"id": paragraph_id, "text": content})

    return ranks

test_result = []

for query in queries:
    reference = multi_agent_query(query)
    # reference = retrieve_with_vector_bm25(query)
    ranks = merge_ranks(reference, documents)
    test_result.append({"response": query, "ranks": ranks})
with open("test_result.json", "w") as f:
    json.dump(test_result, f, indent=4, ensure_ascii=False)

23
explore_response: {'node_ids_for_link_retrieval': ['`1008-5`', '`1010-9`', '`1019-87`', '`1037-웩33`', '`1036-IE89`']}
explore_response: {'node_ids_for_link_retrieval': ['`1037-16`', '`1037-85`']}
response: 질문하신 내용에 대해 답변드리겠습니다.

(질의 1) 향후 통상임금 소송 결과가 확정되어 그 결과를 재무제표에 반영하는 경우, 회계추정의 변경으로 보아 전진적으로 회계처리해야 하는지, 아니면 오류수정으로 보아 과거 재무제표를 소급재작성해야 하는지에 대해 말씀드리면, 일반적으로 소송 결과에 따라 새로운 정보가 발생한 경우 이러한 정보를 반영하는 것은 과거 오류 수정이 아닌 회계추정의 변경으로 간주될 수 있습니다. 특히, 소송 결과가 보고기간 후에 나온 추가적인 증거로 간주된다면, 회계추정의 변경으로 처리할 수 있습니다(이에 대한 관련 내용은 '1037-16'에서 확인하실 수 있습니다).

(질의 2) 질의 1이 회계추정의 변경에 해당한다면, 소송 결과에 따른 관련 비용을 영업비용 중 무엇으로 회계처리해야 하는지에 대해 설명드리면, 일반적으로 관련된 비용은 영업비용(매출원가 또는 판매비와 일반관리비)으로 처리할 수 있으며, 이러한 비용은 회사의 기본적인 운영 및 제반 경비와 관련된 것으로 인식될 수 있습니다. 분류는 구체적인 사안에 따라 다를 수 있지만, 기본적으로 영업비용으로 포함됩니다(관련 기준 내용은 '1019-87'과 '1037-85', '1037-48'에서 확인하실 수 있습니다).

이와 같이 소송 결과에 따른 회계처리는 주의 깊게 다뤄야 하며, 관련 회계 기준에 따라 처리해야 합니다.
22
explore_response: {'node_ids_for_link_retrieval': ['1115-한129.1', '1115-한BC361.2', '1115-39', '1115-40']}
explo

TypeError: expected string or buffer